In [14]:
from src.dataWrangler import EnsembleDataReaderStreamlit
import altair as alt
import pandas as pd
alt.renderers.enable('jupyterlab')
alt.data_transformers.disable_max_rows()

def loadScaleFactorData(selected_pattern, selected_scaleFactor):
    r_edr = EnsembleDataReaderStreamlit(pattern=selected_pattern, scaleFactor=selected_scaleFactor)
    allData = r_edr.loadData()
    return allData

In [2]:
pattern = '1986'
scaleFactor = 200

df = loadScaleFactorData(pattern, scaleFactor)


forecastDate               times FOLC1F   1980   1981   1982   1983  \
0       1986020112 1986-02-01 04:00:00  16073  16034  16034  16034  16034   
1       1986020112 1986-02-01 05:00:00  16200  16159  16159  16159  16159   
2       1986020112 1986-02-01 06:00:00  16300  16257  16257  16258  16257   
3       1986020112 1986-02-01 07:00:00  16359  16316  16316  16316  16315   
4       1986020112 1986-02-01 08:00:00  16377  16333  16333  16334  16333   
...            ...                 ...    ...    ...    ...    ...    ...   
10103   1986022812 1986-03-15 00:00:00  15200   9665   9467  24684  26549   
10104   1986022812 1986-03-15 01:00:00  15200   9600   9393  24551  26009   
10105   1986022812 1986-03-15 02:00:00  15200   9540   9326  24406  25520   
10106   1986022812 1986-03-15 03:00:00  15200   9485   9266  24256  25056   
10107   1986022812 1986-03-15 04:00:00  15200   9434   9211  24098  24611   

        1984   1985   1986  ...   2011   2012   2013   2014   2015   2016  \
0      16034  16034  16034  ...  16034  16034  16034  16034  16034  16034   
1      16159  16159  16159  ...  16159  16159  16159  16159  16159  16159   
2      16257  16257  16265  ...  16257  16258  16257  16257  16257  16257   
3      16316  16315  16340  ...  16315  16318  16316  16315  16316  16315   
4      16334  16333  16378  ...  16333  16338  16333  16332  16334  16332   
...      ...    ...    ...  ...    ...    ...    ...    ...    ...    ...   
10103  31516  12518  18565  ...  39952  14560  11988  11065  12518  73970   
10104  33134  12431  18429  ...  39200  15419  11955  11027  12493  73297   
10105  34821  12355  18296  ...  38572  16353  11941  11000  12480  72522   
10106  36581  12291  18165  ...  38081  17342  11949  10985  12481  71417   
10107  38325  12234  18037  ...  37704  18379  11975  10982  12494  69882   

        2017   2018   2019   2020  
0      16034  16034  16034  16034  
1      16159  16159  16159  16159  
2      16257  16257  16257  16258  
3      16316  16316  16316  16316  
4      16333  16334  16333  16334  
...      ...    ...    ...    ...  
10103  10606  25451  10047  12016  
10104  10600  24993   9993  11960  
10105  10604  24536   9941  11909  
10106  10618  24078   9890  11864  
10107  10641  23625   9841  11823  

[10108 rows x 44 columns]

In [34]:
def getEnsemblePlotData(df: pd.DataFrame, forecastDate: str) -> list[pd.DataFrame]:
    plotDf = df.groupby('forecastDate').get_group(forecastDate)
    plotDf = plotDf.set_index(['forecastDate','times']).stack()
    plotDf.index.names = ['forecastDate','times', 'member']
    plotDf.name = 'flow'
    plotDf = plotDf.reset_index()

    det = plotDf.loc[plotDf.member == 'FOLC1F', :]
    ens = plotDf.loc[plotDf.member != 'FOLC1F', :]
    return det, ens

def getEnsembleChart(df: pd.DataFrame, forecastDate: str, ensembleColor: str) -> alt.Chart:
    
    det, ens = getEnsemblePlotData(df, forecastDate )

    detChart = alt.Chart(det).mark_line(color='black').encode(
    x=alt.X('times\:T').axis(title='Time (PST)'),
    y=alt.Y('flow\:Q').axis(title='Flow (CFS)')
    )

    selection = alt.selection_point(fields = ['member'], bind='legend')
    domain = [str(i) for i in range(1980,2021)]
    range_ = [ensembleColor]*41
    ensChart = alt.Chart(ens).mark_line( strokeWidth=0.5).encode(
        x=alt.X('times\:T').axis(title='Time (PST)'),
        y=alt.Y('flow\:Q').axis(title='Flow (CFS)'),
        color = alt.Color('member').legend(columns=2, symbolLimit=41).scale(domain=domain, range = range_),
        opacity= alt.condition(selection, alt.value(1), alt.value(0.2))
    ).add_params(
        selection
    )

    chart = alt.layer(ensChart, detChart)

    return chart

ensembleColor = 'grey'
forecastDate = '1986020112'
chart = getEnsembleChart(df, forecastDate, ensembleColor)
chart

<VegaLite 5 object>

If you see this message, it means the renderer has not been properly enabled
for the frontend that you are using. For more information, see
https://altair-viz.github.io/user_guide/display_frontends.html#troubleshooting


In [30]:
detChart = alt.Chart(det).mark_line(color='black').encode(
    x=alt.X('times\:T').axis(title='Time (PST)'),
    y=alt.Y('flow\:Q').axis(title='Flow (CFS)')
)
selection = alt.selection_point(fields = ['member'], bind='legend')
domain = [str(i) for i in range(1980,2021)]
range_ = ['red']*41
ensChart = alt.Chart(ens).mark_line( strokeWidth=0.5).encode(
    x=alt.X('times\:T').axis(title='Time (PST)'),
    y=alt.Y('flow\:Q').axis(title='Flow (CFS)'),
    color = alt.Color('member').legend(columns=2, symbolLimit=41).scale(domain=domain, range = range_),
    opacity= alt.condition(selection, alt.value(1), alt.value(0.2))
).add_params(
    selection
)
chart = alt.layer(ensChart, detChart)


In [28]:

ensChart


<VegaLite 5 object>

If you see this message, it means the renderer has not been properly enabled
for the frontend that you are using. For more information, see
https://altair-viz.github.io/user_guide/display_frontends.html#troubleshooting


In [33]:
alt.layer(ensChart, detChart)

<VegaLite 5 object>

If you see this message, it means the renderer has not been properly enabled
for the frontend that you are using. For more information, see
https://altair-viz.github.io/user_guide/display_frontends.html#troubleshooting
